In [ ]:
import plotly.express as px
import pandas as pd
from datatypes import *
from utils import *


# Example DataFrame
df = read_obc(os.path.join(os.getcwd(), "..", "ros2_ws", "src", "simulation", "worlds", "autogen.obc"))

# Create interactive scatter plot
fig = px.scatter_3d(
    df,
    x="x",
    y="y",
    z="z",
    hover_name="id",  # Show label on hover
    title="autogen.obc",
)
fig.update_layout(scene=dict(aspectmode="data"))  # Ensures x, y, z use the same scale
fig.update_traces(marker=dict(size=2))
fig.update_layout(width=800, height=600)  # default ~700  # increase vertical size
fig.show()

In [2]:
import os
from datatypes import *
import plotly.graph_objects as go
from core import main


def plot_camera(name="TopViewCameraFront"):
    vehicle, _ = main()
    camera: Camera = vehicle.get_frame(name)
    photogrammetry = read_obc("/" + os.path.join("home", "workspace", "datasets", "C4L5", "photogrammetry.obc"))

    fig = go.Figure()
    fig.add_trace(go.Image(z=np.asarray(camera.data)))
    fig.add_trace(
        go.Scatter(
            x=camera.features["x"],
            y=camera.features["y"],
            name="feature",
            hovertext=camera.features["id"],
            mode="markers",
            marker=dict(size=15, symbol="x", color="green"),
        )
    )
    convention = SE3(rotation=Rotation.from_euler("YXZ", [90, 0, -90], degrees=True))

    camera_parameter = g2o.CameraParameters(np.mean(camera.intrinsics.focal_length), camera.intrinsics.principal_point, 0)
    mapped = []
    ids = []
    for _, row in photogrammetry.iterrows():
        trow = (camera.parent.transform @ camera.transform @ convention).inverse().apply(row[["x", "y", "z"]].to_numpy())
        projection = camera_parameter.cam_map(trow)
        if (
            projection[0] > 0.0
            and projection[0] < camera.intrinsics.width
            and projection[1] > 0.0
            and projection[1] < camera.intrinsics.height
            and trow[2] > 0.0
        ):
            # mapped.append(np.round(projection * 2) / 2)
            mapped.append(projection)
            ids.append(row["id"])
    df_mapped = pd.DataFrame(mapped, columns=["x", "y"])
    df_mapped["id"] = ids
    fig.add_trace(
        go.Scatter(
            x=df_mapped["x"],
            y=df_mapped["y"],
            name="projections",
            hovertext=df_mapped["id"],
            mode="markers",
            marker=dict(size=8, symbol="x", color="red"),
        )
    )
    fig.update_layout(height=1000, width=1000)
    return fig


plot_camera()

          x         y         z      roll     pitch       yaw  \
0 -0.473313 -0.543712 -0.989117 -2.966498 -2.023878 -0.895872   
1 -0.473694 -0.543747 -0.989917 -2.966523 -2.037625 -0.895159   
2 -0.473694 -0.543747 -0.989917 -2.966523 -2.037625 -0.895159   
3 -0.473085 -0.543598 -0.989320 -2.965496 -2.032928 -0.897901   

                 name  depth                                     path  
0  TopViewCameraFront      2  Vehicle/InitialGuess/TopViewCameraFront  
1   TopViewCameraLeft      2   Vehicle/InitialGuess/TopViewCameraLeft  
2  TopViewCameraRight      2  Vehicle/InitialGuess/TopViewCameraRight  
3   TopViewCameraRear      2   Vehicle/InitialGuess/TopViewCameraRear  


iteration= 0	 chi2= 1906317.868777	 time= 0.000111691	 cumTime= 0.000111691	 edges= 204	 schur= 0	 lambda= 2042.891945	 levenbergIter= 1
iteration= 1	 chi2= 71317.065097	 time= 4.0591e-05	 cumTime= 0.000152282	 edges= 204	 schur= 0	 lambda= 680.963982	 levenbergIter= 1
iteration= 2	 chi2= 351.986338	 time= 3.9116e-05	 cumTime= 0.000191398	 edges= 204	 schur= 0	 lambda= 226.987994	 levenbergIter= 1
iteration= 3	 chi2= 16.708791	 time= 3.8562e-05	 cumTime= 0.00022996	 edges= 204	 schur= 0	 lambda= 75.662665	 levenbergIter= 1
iteration= 4	 chi2= 16.694707	 time= 3.7936e-05	 cumTime= 0.000267896	 edges= 204	 schur= 0	 lambda= 26.300764	 levenbergIter= 1
iteration= 5	 chi2= 16.694707	 time= 3.7386e-05	 cumTime= 0.000305282	 edges= 204	 schur= 0	 lambda= 17.533843	 levenbergIter= 1
iteration= 6	 chi2= 16.694707	 time= 0.000129944	 cumTime= 0.000435226	 edges= 204	 schur= 0	 lambda= 803277671053.130859	 levenbergIter= 9
iteration= 7	 chi2= 16.694707	 time= 4.8649e-05	 cumTime= 0.000483875	 ed